# GITM

In [1]:
from kamodo.kamodo import Kamodo
from plotly.offline import init_notebook_mode, iplot, plot
import plotly.graph_objs as go
init_notebook_mode(connected = True)
import plotly
import spacepy
import os

In [2]:
from kamodo import readers

In [3]:
from kamodo.readers.gitm import gitm as gitm
from kamodo.readers.gitm import gitm_alt_plots as gap
from kamodo.readers.gitm import gitm_plot_rout as gpr

Qin-Denton/OMNI2 data not found in current format. This module has limited functionality.
Run spacepy.toolbox.update(QDomni=True) to download data
solar_rout.py unavailable: can't load add_solar_terminator, add_subsolar_point
PySolar not installed, cannot load find_sunside_twilight_sza


In [4]:
#datafile = '../../../../data/GITMdefault/3DLST_t150317_180000.bin'
#datafile = '../../../../data/GITMdefault/3DLST_t150318_120000.bin'
#datafile = '../../../../data/GITMwSWMF/3DLST_t150317_180000.bin'
#datafile = '../../../../data/GITMwSWMF/3DLST_t150318_120000.bin'

import glob
files = glob.glob('../../../../data/IN/*.bin')
#files = glob.glob('../../../../data/jasoon_shim_071418_IT_1/*.bin')
datafile = files[0]
datafile

'../../../../data/IN/3DLST_t150317_080000.bin'

In [5]:
latkey = "dLat"
lonkey = "dLon"
altkey = "Altitude"
gData = gitm.GitmBin(datafile)

In [6]:
gda = gData[altkey]
gda.attrs

import numpy as np

from kamodo.kamodo import Kamodo

lon = np.unique(gData[lonkey])
lat = np.unique(gData[latkey])
alt = np.unique(gData[altkey])

In [7]:
sphere = Kamodo()
sphere['theta'] = lambda lat: np.pi*lat/180
sphere['phi'] = lambda lon: np.pi*lon/180
sphere['r'] = lambda alt: alt + 6.3781E6
sphere['x(lon,lat,alt)'] = 'r*cos(theta)*cos(phi)'
sphere['y(lon,lat,alt)'] = 'r*cos(theta)*sin(phi)'
sphere['z(alt,lat)'] = 'r*sin(theta)'
#sphere

In [8]:
from scipy.interpolate import RegularGridInterpolator

def wrap_interpolator(lon, lat, alt, v):
    rgi = RegularGridInterpolator((lon, lat, alt), v, bounds_error = False)
    def wrapped(lon, lat, alt):
        return rgi((lon,lat,alt))
    return wrapped
    

In [9]:
def kamodofy_names(name, name_maps):
    """replaces all substrings in name with those given by name_maps"""
    for old, new in name_maps:
        name = name.replace(old, new)
    return name

In [10]:
kamodo = Kamodo(verbose = False)

for k,v in gData.items():
    var_name = kamodofy_names(k,[
            ('Vn (up) (m/s)', 'V_n__u__p [m/s]'),
            ('Vi (east) (m/s)', 'V_i__e__a__s__t [m/s]'),
            ('Vi (up) (m/s)', 'V_i__u__p [m/s]'),
            ('Vi (north) (m/s)', 'V_i__n__o__r__t__h [m/s]'),
            ('Vn (north) (m/s)', 'V_n__n__o__r__t__h [m/s]'),
            ('Vn (east) (m/s)', 'V_n__e__a__s__t [m/s]'),
            ('Rho (kg/m3)', 'rho (kg/m^3)'),
            ('O_4SP_!U+!N', 'O!U+_4SP_!N'),
            ('LT', 'lt [hours]'),
            ('V!Dn!N (up,N(!U4!NS)           )', 'V_N__u__pCOMMALEFT4SRIGHT [m/s]'),
            ('N(!U2!ND)','N__2D [kg/m^3]'),
            (" ", ''),
            ("O(!U3!NP)", "OLEFT3PRIGHT"),
            ('(','['),
            (')',']'),
            ('!D', '_'),
            ('!N',''),
            ('[/m3]','[1/m^3]'),
            ('!U','__'),
            ('+', 'plus'),
            ('e-', 'eminus'),
        ])
    if k not in ['time']:
        try:
            kamodo[var_name] = wrap_interpolator(lon, lat, alt, v)
        except:
            print (k)
            raise


from kamodo.kamodo import kamodofy

# define lat, lon, an alt in terms of r, theta, phi with defaults that correspond to the model
@kamodofy(units = 'degrees')
def LAT(theta = sphere.theta(lat[1:-1])):
    return 180*theta/np.pi


@kamodofy(units = 'degrees')
def LON(phi = sphere.phi(lon[1:-1])):
    return 180*phi/np.pi+180


@kamodofy(units = 'm')
def ALT(r = sphere.r(alt[1:-1])):
    '''must generate altitude in meters'''
    return r - 6.3781E6

kamodo['ALT'] = ALT
kamodo['LON'] = LON
kamodo['LAT'] = LAT

kamodo['r'] = 'sqrt(x**2 + y**2 + z**2)'
kamodo['theta'] = 'asin(z/r)' #colatitude
kamodo['phi'] = 'atan2(y,x)'
#kamodo


In [11]:
newvars = ["rho", "NeutralTemperature", "V_n__u__p", "V_i__e__a__s__t", "NO", "N_2", "NO__plus", "OLEFT3PRIGHT", "O__plus_4SP_", "eminus", "V_i__u__p", "N_2__plus", "V_i__n__o__r__t__h", "V_n__e__a__s__t", "O_2__plus", "O_2", "V_n__n__o__r__t__h"]
#newvars

In [12]:
ilat = np.linspace(-90, 90, 91)
ilon = np.linspace(0, 360, 181)
ialt = np.array([400000.])

In [13]:
# Have to make lat into a column
def rhoK(ilon, ilat, ialt):
    return kamodo.rho(ilon, ilat.reshape(-1,1), ialt)
def NeutralTemperatureK(ilon, ilat, ialt):
    return kamodo.NeutralTemperature(ilon, ilat.reshape(-1,1), ialt)
def V_n__u__pK(ilon, ilat, ialt):
    return kamodo.V_n__u__p(ilon, ilat.reshape(-1,1), ialt)
def V_i__e__a__s__tK(ilon, ilat, ialt):
    return kamodo.V_i__e__a__s__t(ilon, ilat.reshape(-1,1), ialt)
def NOK(ilon, ilat, ialt):
    return kamodo.NO(ilon, ilat.reshape(-1,1), ialt)
def N_2K(ilon, ilat, ialt):
    return kamodo.N_2(ilon, ilat.reshape(-1,1), ialt)
def NO__plusK(ilon, ilat, ialt):
    return kamodo.NO__plus(ilon, ilat.reshape(-1,1), ialt)
def OLEFT3PRIGHTK(ilon, ilat, ialt):
    return kamodo.OLEFT3PRIGHT(ilon, ilat.reshape(-1,1), ialt)
def O__plus_4SP_K(ilon, ilat, ialt):
    return kamodo.O__plus_4SP_(ilon, ilat.reshape(-1,1), ialt)
def eminusK(ilon, ilat, ialt):
    return kamodo.eminus(ilon, ilat.reshape(-1,1), ialt)
def V_i__u__pK(ilon, ilat, ialt):
    return kamodo.V_i__u__p(ilon, ilat.reshape(-1,1), ialt)
def N_2__plusK(ilon, ilat, ialt):
    return kamodo.N_2__plus(ilon, ilat.reshape(-1,1), ialt)
def V_i__n__o__r__t__hK(ilon, ilat, ialt):
    return kamodo.V_i__n__o__r__t__h(ilon, ilat.reshape(-1,1), ialt)
def V_n__e__a__s__tK(ilon, ilat, ialt):
    return kamodo.V_n__e__a__s__t(ilon, ilat.reshape(-1,1), ialt)
def O_2__plusK(ilon, ilat, ialt):
    return kamodo.O_2__plus(ilon, ilat.reshape(-1,1), ialt)
def O_2K(ilon, ilat, ialt):
    return kamodo.O_2(ilon, ilat.reshape(-1,1), ialt)
def V_n__n__o__r__t__hK(ilon, ilat, ialt):
    return kamodo.V_n__n__o__r__t__h(ilon, ilat.reshape(-1,1), ialt)

In [14]:
kamodo['rhoK(ilon, ilat, ialt)'] = rhoK
kamodo['NeutralTemperatureK(ilon, ilat, ialt)'] = NeutralTemperatureK
kamodo['V_n__u__pK(ilon, ilat, ialt)'] = V_n__u__pK
kamodo['V_i__e__a__s__tK(ilon, ilat, ialt)'] = V_i__e__a__s__tK
kamodo['NOK(ilon, ilat, ialt)'] = NOK
kamodo['N_2K(ilon, ilat, ialt)'] = N_2K
kamodo['NO__plusK(ilon, ilat, ialt)'] = NO__plusK
kamodo['OLEFT3PRIGHTK(ilon, ilat, ialt)'] = OLEFT3PRIGHTK
kamodo['O__plus_4SP_K(ilon, ilat, ialt)'] = O__plus_4SP_K
kamodo['eminusK(ilon, ilat, ialt)'] = eminusK
kamodo['V_i__u__pK(ilon, ilat, ialt)'] = V_i__u__pK
kamodo['N_2__plusK(ilon, ilat, ialt)'] = N_2__plusK
kamodo['V_i__n__o__r__t__hK(ilon, ilat, ialt)'] = V_i__n__o__r__t__hK
kamodo['V_n__e__a__s__tK(ilon, ilat, ialt)'] = V_n__e__a__s__tK
kamodo['O_2__plusK(ilon, ilat, ialt)'] = O_2__plusK
kamodo['O_2K(ilon, ilat, ialt)'] = O_2K
kamodo['V_n__n__o__r__t__hK(ilon, ilat, ialt)'] = V_n__n__o__r__t__hK

In [15]:
resultsALL = []

results = kamodo.evaluate('rhoK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['rhoK'])

results = kamodo.evaluate('NeutralTemperatureK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['NeutralTemperatureK'])

results = kamodo.evaluate('V_n__u__pK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['V_n__u__pK'])

results = kamodo.evaluate('V_i__e__a__s__tK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['V_i__e__a__s__tK'])

results = kamodo.evaluate('NOK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['NOK'])

results = kamodo.evaluate('N_2K', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['N_2K'])

results = kamodo.evaluate('NO__plusK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['NO__plusK'])

results = kamodo.evaluate('OLEFT3PRIGHTK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['OLEFT3PRIGHTK'])

results = kamodo.evaluate('O__plus_4SP_K', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['O__plus_4SP_K'])

results = kamodo.evaluate('eminusK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['eminusK'])

results = kamodo.evaluate('V_i__u__pK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['V_i__u__pK'])

results = kamodo.evaluate('N_2__plusK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['N_2__plusK'])

results = kamodo.evaluate('V_i__n__o__r__t__hK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['V_i__n__o__r__t__hK'])

results = kamodo.evaluate('V_n__e__a__s__tK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['V_n__e__a__s__tK'])

results = kamodo.evaluate('O_2__plusK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['O_2__plusK'])

results = kamodo.evaluate('O_2K', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['O_2K'])

results = kamodo.evaluate('V_n__n__o__r__t__hK', ilon = ilon, ilat = ilat, ialt=ialt)
resultsALL.append(results['V_n__n__o__r__t__hK'])

In [16]:
#len(resultsALL)
#resultsALL

In [17]:
head, tail = os.path.split(datafile)
idx1 = tail.find('_')
idx2 = tail.find('.')
newfile = '400km' + tail[idx1:idx2] + '.dat'
outF = open(newfile, "w")
header="#GITM 2x2 degree grid extracted at 400km\n#run = nnn\n#datafile = " + tail + "\nLatitude Longitude " + " ".join("%s" % n for n in newvars) + "\n"
outF.write(header)
i = 0
while i < len(ilat):
    latv = ilat[i]
    j = 0
    while j < len(ilon):
        lonv = ilon[j]
        vv = []
        n = 0
        while n < len(newvars):
            vv.append(resultsALL[n][i][j])
            n += 1
        line = '{:.0f} {:.0f} '.format(latv, lonv) + " ".join("%.5e" % n for n in vv) + "\n"
        outF.write(line)
        j += 1
    i += 1

outF.close()

# Plotting and other misc stuff ...

In [19]:
# 3D plot of density at 400km altitude
iplot(kamodo.plot(rhoK = dict(ilon = ilon, ilat = ilat, ialt = ialt)))

In [20]:
def rhoK2D(ilon, ilat):
    return kamodo.rho(ilon, ilat.reshape(-1,1), ialt)

kamodo['rhoK2D(ilon, ilat)'] = rhoK2D

In [21]:
# 2D plot of density at 400km altitude
iplot(kamodo.plot(rhoK2D = dict(ilon = ilon, ilat = ilat)))

In [22]:
# 3D plot of density at 400km altitude in spherical coords
kamodo['Srho'] = 'rho(LON, LAT, ALT)'
alt_slice = 400000.
llon, llat = np.meshgrid(np.array(lon), np.array(lat))
iplot(kamodo.plot(Srho = dict(
        x = sphere.x(llon, llat, alt_slice),
        y = sphere.y(llon, llat, alt_slice),
        z = sphere.z(alt_slice, llat))))

In [22]:
results = kamodo.evaluate('rhoK2D', ilon = ilon, ilat = ilat)
results['rhoK2D']
results

{'ilon': array([  0.,   2.,   4.,   6.,   8.,  10.,  12.,  14.,  16.,  18.,  20.,
         22.,  24.,  26.,  28.,  30.,  32.,  34.,  36.,  38.,  40.,  42.,
         44.,  46.,  48.,  50.,  52.,  54.,  56.,  58.,  60.,  62.,  64.,
         66.,  68.,  70.,  72.,  74.,  76.,  78.,  80.,  82.,  84.,  86.,
         88.,  90.,  92.,  94.,  96.,  98., 100., 102., 104., 106., 108.,
        110., 112., 114., 116., 118., 120., 122., 124., 126., 128., 130.,
        132., 134., 136., 138., 140., 142., 144., 146., 148., 150., 152.,
        154., 156., 158., 160., 162., 164., 166., 168., 170., 172., 174.,
        176., 178., 180., 182., 184., 186., 188., 190., 192., 194., 196.,
        198., 200., 202., 204., 206., 208., 210., 212., 214., 216., 218.,
        220., 222., 224., 226., 228., 230., 232., 234., 236., 238., 240.,
        242., 244., 246., 248., 250., 252., 254., 256., 258., 260., 262.,
        264., 266., 268., 270., 272., 274., 276., 278., 280., 282., 284.,
        286., 288., 290., 292.

In [23]:
for k,v in gData.items():
    print(k)

time
Longitude
Latitude
Altitude
Rho (kg/m3)
O(!U3!NP)            (/m3)
O!D2!N               (/m3)
N!D2!N               (/m3)
NO                   (/m3)
Vn (east) (m/s)
Vn (north) (m/s)
Vn (up) (m/s)
O_4SP_!U+!N          (/m3)
O!D2!U+!N            (/m3)
N!D2!U+!N            (/m3)
NO!U+!N              (/m3)
e-                   (/m3)
Vi (east) (m/s)
Vi (north) (m/s)
Vi (up) (m/s)
Neutral Temperature (K)
dLat
dLon
LT


In [25]:
print (gData['Rho (kg/m3)'].attrs)
#print gData.attrs

{'units': 'kg \\, m^{-3}', 'scale': 'exponential', 'name': 'Neutral Density'}
